In [21]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

class LJParticles:
    def __init__(self, N=11, L=10.0, temperature=1.0, dt=0.01):
        # Initialize system parameters
        self.N = N
        self.L = L  # Square box (L×L)
        self.dt = dt
        self.initial_temperature = temperature

        # Arrays for positions, velocities, and accelerations
        self.x = np.zeros(N)
        self.y = np.zeros(N)
        self.vx = np.zeros(N)
        self.vy = np.zeros(N)
        self.ax = np.zeros(N)
        self.ay = np.zeros(N)

        # Tracking
        self.time = 0.0
        self.potential_energy = 0.0
        self.kinetic_energy = 0.0
        self.total_energy = 0.0

        # Initialize particles on a square lattice with 8×8 grid
        self.set_initial_conditions()

        # Calculate initial accelerations and energy
        self.compute_acceleration()
        self.compute_energy()

    def set_initial_conditions(self):
        """Set positions and velocities according to Figure 8.4"""
        for i in range(self.N):
            self.x[i] = self.L / 2                   # All particles at center of x-axis
            self.y[i] = (i - 0.5) * self.L / self.N  # Evenly spaced along y-axis
            self.vx[i] = 1                           # All particles moving in +x direction
            self.vy[i] = 0                           # No velocity in y direction

            # (b) change the velocity of particle 6
            self.vx[6] = 0.99999
            self.vy[6] = 0.00001

    def pbc_separation(self, dr, L):
        """Apply minimum image convention for distance"""
        if dr > 0.5 * L:
            return dr - L
        elif dr < -0.5 * L:
            return dr + L
        return dr

    def pbc_position(self, r, L):
        """Apply periodic boundary conditions to position"""
        return r % L

    def compute_acceleration(self):
        """Calculate forces and accelerations using Lennard-Jones potential"""
        # Reset accelerations and potential energy
        self.ax = np.zeros(self.N)
        self.ay = np.zeros(self.N)
        self.potential_energy = 0.0

        # Loop over all pairs of particles
        for i in range(self.N - 1):
            for j in range(i + 1, self.N):
                # Calculate separation with periodic boundary conditions
                dx = self.pbc_separation(self.x[i] - self.x[j], self.L)
                dy = self.pbc_separation(self.y[i] - self.y[j], self.L)

                # Square distance
                r2 = dx**2 + dy**2

                # Compute Lennard-Jones force and potential
                if r2 > 0:  # Avoid division by zero
                    r2i = 1.0 / r2
                    r6i = r2i**3
                    f_mag= 48.0 * r2i * r6i * (r6i - 0.5)

                    # Update accelerations
                    self.ax[i] += f_mag * dx
                    self.ay[i] += f_mag * dy
                    self.ax[j] -= f_mag * dx
                    self.ay[j] -= f_mag * dy

                    # Update potential energy
                    self.potential_energy += 4.0 * r6i * (r6i - 1.0)

    def compute_energy(self):
        """Calculate the kinetic energy and total energy"""
        self.kinetic_energy = 0.5 * np.sum(self.vx**2 + self.vy**2)
        self.total_energy = self.kinetic_energy + self.potential_energy

    def get_temperature(self):
        """Calculate the current temperature based on equation (8.5)"""
        # For 2D system with N particles
        return np.sum(self.vx**2 + self.vy**2) / (2 * self.N)

    def step(self):
        """Perform one time step using the Velocity Verlet algorithm"""
        # First half of velocity update
        self.vx += 0.5 * self.dt * self.ax
        self.vy += 0.5 * self.dt * self.ay

        # Update positions
        self.x += self.dt * self.vx
        self.y += self.dt * self.vy

        # Apply periodic boundary conditions
        for i in range(self.N):
            self.x[i] = self.pbc_position(self.x[i], self.L)
            self.y[i] = self.pbc_position(self.y[i], self.L)

        # Calculate new accelerations
        self.compute_acceleration()

        # Second half of velocity update
        self.vx += 0.5 * self.dt * self.ax
        self.vy += 0.5 * self.dt * self.ay

        # Update energy and time
        self.compute_energy()
        self.time += self.dt

# Create the simulation
sim = LJParticles(N=11, L=10.0, temperature=1.0, dt=0.01)

# Run simulation and record positions
num_steps = 500
positions_history = []
energy_values = []
temp_values = []

# Save initial positions
positions_history.append((sim.x.copy(), sim.y.copy()))

# Run the simulation
for i in range(num_steps):
    sim.step()
    energy_values.append(sim.total_energy)
    temp_values.append(sim.get_temperature())

    # Save positions every few steps to make the animation smoother
    if i % 5 == 0:
        positions_history.append((sim.x.copy(), sim.y.copy()))

# Create animation
fig, ax = plt.subplots(figsize=(8, 8))
ax.set_xlim(0, sim.L)
ax.set_ylim(0, sim.L)
ax.set_xlabel('x')
ax.set_ylabel('y')
ax.set_title('Lennard-Jones Particles Simulation (N=11, L=10)')
ax.grid(True)

# Draw boundary box
ax.plot([0, sim.L, sim.L, 0, 0], [0, 0, sim.L, sim.L, 0], 'k-')
plt.close()

# Create scatter plot for particles
particles = ax.scatter([], [], s=30)

# Animation function
def init():
    particles.set_offsets(np.c_[[], []])
    return [particles]

def animate(i):
    x, y = positions_history[i]
    particles.set_offsets(np.c_[x, y])
    return [particles]

# Create animation
anim = FuncAnimation(
    fig, animate, init_func=init,
    frames=len(positions_history), interval=50, blit=True
)

# Display animation
HTML(anim.to_jshtml())

In [29]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML

class LJParticles:
    def __init__(self, N=11, L=10.0, dt=0.01):
        # Initialize system parameters
        self.N = N
        self.L = L  # Square box (L×L)
        self.dt = dt
        self.original_dt = dt  # Store the original dt value

        # Arrays for positions, velocities, and accelerations
        self.x = np.zeros(N)
        self.y = np.zeros(N)
        self.vx = np.zeros(N)
        self.vy = np.zeros(N)
        self.ax = np.zeros(N)
        self.ay = np.zeros(N)

        # Tracking
        self.time = 0.0
        self.potential_energy = 0.0
        self.kinetic_energy = 0.0
        self.total_energy = 0.0

        # Save initial state for comparison
        self.initial_x = None
        self.initial_y = None
        self.initial_vx = None
        self.initial_vy = None

        # Initialize positions and velocities according to Figure 8.4
        self.set_initial_conditions()

        # Save the initial state
        self.save_initial_state()

        # Calculate initial accelerations and energy
        self.compute_acceleration()
        self.compute_energy()

    def save_initial_state(self):
        """Save the initial state for comparison"""
        self.initial_x = self.x.copy()
        self.initial_y = self.y.copy()
        self.initial_vx = self.vx.copy()
        self.initial_vy = self.vy.copy()

    def set_initial_conditions(self):
        """Set positions and velocities according to Figure 8.4"""
        for i in range(self.N):
            self.x[i] = self.L / 2                   # All particles at center of x-axis
            self.y[i] = (i - 0.5) * self.L / self.N  # Evenly spaced along y-axis
            self.vx[i] = 1                           # All particles moving in +x direction
            self.vy[i] = 0                           # No velocity in y direction

        # Change particle 6's velocity as requested (optional)
        if self.N > 6:  # Make sure we have at least 7 particles
            self.vx[6] = 0.99999
            self.vy[6] = 0.00001

    def pbc_separation(self, dr, L):
        """Apply minimum image convention for distance"""
        if dr > 0.5 * L:
            return dr - L
        elif dr < -0.5 * L:
            return dr + L
        return dr

    def pbc_position(self, r, L):
        """Apply periodic boundary conditions to position"""
        return r % L

    def compute_acceleration(self):
        """Calculate forces and accelerations using Lennard-Jones potential"""
        # Reset accelerations and potential energy
        self.ax = np.zeros(self.N)
        self.ay = np.zeros(self.N)
        self.potential_energy = 0.0

        # Loop over all pairs of particles
        for i in range(self.N - 1):
            for j in range(i + 1, self.N):
                # Calculate separation with periodic boundary conditions
                dx = self.pbc_separation(self.x[i] - self.x[j], self.L)
                dy = self.pbc_separation(self.y[i] - self.y[j], self.L)

                # Square distance
                r2 = dx**2 + dy**2

                # Compute Lennard-Jones force and potential
                if r2 > 0:  # Avoid division by zero
                    r2i = 1.0 / r2
                    r6i = r2i**3
                    f_mag= 48.0 * r2i * r6i * (r6i - 0.5)

                    # Update accelerations
                    self.ax[i] += f_mag * dx
                    self.ay[i] += f_mag * dy
                    self.ax[j] -= f_mag * dx
                    self.ay[j] -= f_mag * dy

                    # Update potential energy
                    self.potential_energy += 4.0 * r6i * (r6i - 1.0)

    def compute_energy(self):
        """Calculate the kinetic energy and total energy"""
        self.kinetic_energy = 0.5 * np.sum(self.vx**2 + self.vy**2)
        self.total_energy = self.kinetic_energy + self.potential_energy

    def get_temperature(self):
        """Calculate the current temperature"""
        # For 2D system with N particles
        return np.sum(self.vx**2 + self.vy**2) / (2 * self.N)

    def get_momentum(self):
        """Calculate total momentum of the system"""
        px = np.sum(self.vx)
        py = np.sum(self.vy)
        return np.sqrt(px**2 + py**2)

    def reverse_time(self):
        """Reverse the direction of time by flipping all velocities"""
        self.vx = -self.vx
        self.vy = -self.vy

    def change_dt(self, new_dt):
        """Change the time step"""
        self.dt = new_dt

    def step(self):
        """Perform one time step using the Velocity Verlet algorithm"""
        # First half of velocity update
        self.vx += 0.5 * self.dt * self.ax
        self.vy += 0.5 * self.dt * self.ay

        # Update positions
        self.x += self.dt * self.vx
        self.y += self.dt * self.vy

        # Apply periodic boundary conditions
        for i in range(self.N):
            self.x[i] = self.pbc_position(self.x[i], self.L)
            self.y[i] = self.pbc_position(self.y[i], self.L)

        # Calculate new accelerations
        self.compute_acceleration()

        # Second half of velocity update
        self.vx += 0.5 * self.dt * self.ax
        self.vy += 0.5 * self.dt * self.ay

        # Update energy and time
        self.compute_energy()
        self.time += self.dt

# Create simulation
forward_steps = 200
total_steps = 400
sim = LJParticles(N=11, L=10.0, dt=0.01)

# Arrays to track positions and deviations
positions_history = []

# Save initial positions
positions_history.append((sim.x.copy(), sim.y.copy()))

# First run forward
for i in range(forward_steps):
    sim.step()

    if i % 5 == 0:  # Save every 5th step for smoother animation
        positions_history.append((sim.x.copy(), sim.y.copy()))

# Reverse time
sim.reverse_time()

# Run backward
for i in range(forward_steps, total_steps):
    sim.step()

    if i % 5 == 0:  # Save every 5th step for smoother animation
        positions_history.append((sim.x.copy(), sim.y.copy()))


# Create animations and plots
fig, ax = plt.subplots(figsize=(12, 10))
ax.set_xlim(0, sim.L)
ax.set_ylim(0, sim.L)
ax.set_xlabel('x')
ax.set_ylabel('y')
ax.set_title('Lennard-Jones Particles with Time Reversal')
ax.grid(True)
plt.close()

# Create scatter plot for particles
particles = ax.scatter([], [], s=50)

# Animation function
def init():
    particles.set_offsets(np.c_[[], []])
    return [particles]

def animate(i):
    x, y = positions_history[i]
    particles.set_offsets(np.c_[x, y])
    return [particles]

# Create animation
anim = FuncAnimation(
    fig, animate, init_func=init,
    frames=len(positions_history), interval=50, blit=False
)

# Display animation
HTML(anim.to_jshtml())